# RFM Customer Segmentation Analytics

## Create Recency, Frequency, and Monetary variables using existing variables.

In [27]:
WITH CustomerRFM AS (
    SELECT 
        c.CustomerID,
        -- Recency - days since last purchase (lower is better)
        DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency,
        -- Frequency - total number of orders
        COUNT(DISTINCT soh.SalesOrderID) AS Frequency,
        -- Monetary - total spend amount
        SUM(soh.TotalDue) AS Monetary,
        -- Additional data points for segmentation analysis
        MIN(soh.OrderDate) AS FirstPurchaseDate,
        MAX(soh.OrderDate) AS LastPurchaseDate
    FROM 
        Sales.Customer c
        JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
    GROUP BY 
        c.CustomerID
)
SELECT TOP 20 * 
FROM CustomerRFM
ORDER BY Monetary DESC;

(20 rows affected)

Total execution time: 00:00:00.073

CustomerID Recency Frequency Monetary FirstPurchaseDate LastPurchaseDate 29818 4063 12 989184.082 2011-07-01 00:00:00.000 2014-03-31 00:00:00.000 29715 4032 12 961675.8596 2011-08-01 00:00:00.000 2014-05-01 00:00:00.000 29722 4032 12 954021.9235 2011-08-01 00:00:00.000 2014-05-01 00:00:00.000 30117 4063 12 919801.8188 2011-07-01 00:00:00.000 2014-03-31 00:00:00.000 29614 4093 12 901346.856 2011-05-31 00:00:00.000 2014-03-01 00:00:00.000 29639 4032 12 887090.4106 2011-08-01 00:00:00.000 2014-05-01 00:00:00.000 29701 4032 8 841866.5522 2012-07-31 00:00:00.000 2014-05-01 00:00:00.000 29617 4063 12 834475.9271 2011-07-01 00:00:00.000 2014-03-31 00:00:00.000 29994 4093 12 824331.7682 2011-05-31 00:00:00.000 2014-03-01 00:00:00.000 29646 4093 12 820383.5466 2011-05-31 00:00:00.000 2014-03-01 00:00:00.000 29580 4093 12 815914.2534 2011-05-31 00:00:00.000 2014-03-01 00:00:00.000 29827 4093 12 801766.21 2011-05-31 00:00:00.000 2014-03-01 00:00:00.000 29497 4093 12 789884.2937 2011-05-31 00:00:00.000 2014-03-01 00:00:00.000 29716 4063 12 781073.7175 2011-07-01 00:00:00.000 2014-03-31 00:00:00.000 29913 4063 8 757449.6804 2012-06-30 00:00:00.000 2014-03-31 00:00:00.000 30103 4063 8 725867.1659 2012-06-30 00:00:00.000 2014-03-31 00:00:00.000 29957 4032 8 718258.8109 2012-07-31 00:00:00.000 2014-05-01 00:00:00.000 29523 4063 12 696703.605 2011-07-01 00:00:00.000 2014-03-31 00:00:00.000 29616 4063 8 695242.2258 2012-06-30 00:00:00.000 2014-03-31 00:00:00.000 30048 4093 8 678828.8377 2012-05-30 00:00:00.000 2014-03-01 00:00:00.000

## Assigning RFM Scores

Next, we'll convert the raw metrics into quintile scores (1-5 scale), where 5 is the best score and 1 is the worst:

In [28]:
WITH CustomerRFM AS (
    SELECT 
        c.CustomerID,
        DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency,
        COUNT(DISTINCT soh.SalesOrderID) AS Frequency,
        SUM(soh.TotalDue) AS Monetary
    FROM 
        Sales.Customer c
        JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
    GROUP BY 
        c.CustomerID
),
RFM_Scores AS (
    SELECT 
        CustomerID,
        Recency,
        Frequency,
        Monetary,
        -- Convert raw metrics to quintile scores (1-5)
        -- For Recency, LOWER values are BETTER, so we use DESC
        NTILE(5) OVER (ORDER BY Recency ASC) AS R_Score,
        -- For Frequency and Monetary, HIGHER values are BETTER
        NTILE(5) OVER (ORDER BY Frequency DESC) AS F_Score,
        NTILE(5) OVER (ORDER BY Monetary DESC) AS M_Score
    FROM 
        CustomerRFM
)
SELECT 
    CustomerID,
    Recency,
    Frequency,
    Monetary,
    R_Score,
    F_Score,
    M_Score,
    -- Create a combined RFM score (concatenated string)
    CAST(R_Score AS VARCHAR) + CAST(F_Score AS VARCHAR) + CAST(M_Score AS VARCHAR) AS RFM_Score,
    -- Create a numeric RFM score for easier sorting
    (R_Score * 100) + (F_Score * 10) + M_Score AS RFM_Score_Numeric
FROM 
    RFM_Scores
ORDER BY 
    RFM_Score_Numeric DESC;
    

(19119 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.579

CustomerID Recency Frequency Monetary R_Score F_Score M_Score RFM_Score RFM_Score_Numeric 12722 4269 1 43.6144 5 5 5 555 555 20789 4263 1 43.6144 5 5 5 555 555 23272 4284 1 43.6144 5 5 5 555 555 22839 4329 1 43.3713 5 5 5 555 555 29324 4272 1 43.0729 5 5 5 555 555 17740 4280 1 43.0729 5 5 5 555 555 22185 4280 1 43.0729 5 5 5 555 555 26179 4280 1 43.0729 5 5 5 555 555 25669 4273 1 43.0729 5 5 5 555 555 29052 4274 1 43.0729 5 5 5 555 555 27152 4275 1 43.0729 5 5 5 555 555 26897 4284 1 43.0729 5 5 5 555 555 23959 4310 1 43.0729 5 5 5 555 555 26037 4313 1 43.0729 5 5 5 555 555 23937 4315 1 43.0729 5 5 5 555 555 29268 4315 1 43.0729 5 5 5 555 555 19177 4314 1 43.0729 5 5 5 555 555 23140 4318 1 43.0729 5 5 5 555 555 23602 4319 1 43.0729 5 5 5 555 555 27482 4300 1 43.0729 5 5 5 555 555 22835 4292 1 43.0729 5 5 5 555 555 23897 4292 1 43.0729 5 5 5 555 555 25512 4291 1 43.0729 5 5 5 555 555 27002 4324 1 43.0729 5 5 5 555 555 22705 4323 1 43.0729 5 5 5 555 555 20940 4322 1 43.0729 5 5 5 555 555 26401 4322 1 43.0729 5 5 5 555 555 23941 4337 1 43.0729 5 5 5 555 555 23690 4333 1 43.0729 5 5 5 555 555 24299 4292 1 42.9624 5 5 5 555 555 24297 4318 1 42.9624 5 5 5 555 555 24292 4321 1 42.9624 5 5 5 555 555 25378 4313 1 42.9624 5 5 5 555 555 14174 4312 1 42.9624 5 5 5 555 555 24397 4304 1 42.9624 5 5 5 555 555 24451 4262 1 42.9624 5 5 5 555 555 14422 4269 1 42.9624 5 5 5 555 555 27903 4278 1 42.9624 5 5 5 555 555 25045 4333 1 42.9624 5 5 5 555 555 24516 4326 1 42.9624 5 5 5 555 555 24820 4330 1 42.9624 5 5 5 555 555 11350 4329 1 42.5094 5 5 5 555 555 24513 4264 1 42.9624 5 5 5 555 555 28979 4282 1 41.9569 5 5 5 555 555 28638 4268 1 41.9569 5 5 5 555 555 28813 4293 1 41.9569 5 5 5 555 555 16413 4301 1 41.9127 5 5 5 555 555 19056 4316 1 41.9127 5 5 5 555 555 14707 4322 1 41.2055 5 5 5 555 555 17092 4325 1 41.1834 5 5 5 555 555 21111 4326 1 41.1834 5 5 5 555 555 24550 4330 1 41.1834 5 5 5 555 555 22163 4330 1 41.1834 5 5 5 555 555 23785 4331 1 41.1834 5 5 5 555 555 23109 4317 1 41.1834 5 5 5 555 555 22242 4300 1 41.1834 5 5 5 555 555 22060 4299 1 41.1834 5 5 5 555 555 20929 4299 1 41.1834 5 5 5 555 555 14820 4320 1 41.1834 5 5 5 555 555 23046 4318 1 41.1834 5 5 5 555 555 23578 4290 1 41.1834 5 5 5 555 555 23089 4295 1 41.1834 5 5 5 555 555 17842 4287 1 41.1834 5 5 5 555 555 22145 4284 1 41.1834 5 5 5 555 555 21739 4271 1 41.1834 5 5 5 555 555 20868 4271 1 41.1834 5 5 5 555 555 23044 4266 1 41.1834 5 5 5 555 555 13485 4319 1 40.8408 5 5 5 555 555 21453 4298 1 40.8408 5 5 5 555 555 12838 4276 1 40.8408 5 5 5 555 555 14943 4269 1 40.8408 5 5 5 555 555 13234 4334 1 40.8408 5 5 5 555 555 22154 4330 1 40.8408 5 5 5 555 555 14811 4289 1 40.8077 5 5 5 555 555 20580 4293 1 40.8077 5 5 5 555 555 25435 4315 1 40.432 5 5 5 555 555 12505 4305 1 40.432 5 5 5 555 555 25091 4268 1 40.432 5 5 5 555 555 24395 4275 1 40.432 5 5 5 555 555 24742 4278 1 40.432 5 5 5 555 555 24393 4327 1 40.432 5 5 5 555 555 25156 4323 1 40.432 5 5 5 555 555 24486 4333 1 40.432 5 5 5 555 555 24989 4331 1 40.432 5 5 5 555 555 26788 4330 1 40.0784 5 5 5 555 555 26861 4330 1 40.0784 5 5 5 555 555 27322 4273 1 40.0784 5 5 5 555 555 27930 4274 1 40.0784 5 5 5 555 555 29394 4284 1 40.0784 5 5 5 555 555 26184 4268 1 40.0784 5 5 5 555 555 23928 4268 1 40.0784 5 5 5 555 555 27382 4262 1 40.0784 5 5 5 555 555 27336 4263 1 40.0784 5 5 5 555 555 29409 4263 1 40.0784 5 5 5 555 555 23964 4309 1 40.0784 5 5 5 555 555 26838 4317 1 40.0784 5 5 5 555 555 27680 4268 1 39.4706 5 5 5 555 555 17908 4295 1 39.4706 5 5 5 555 555 26291 4295 1 38.9292 5 5 5 555 555 26470 4291 1 38.9292 5 5 5 555 555 25849 4328 1 38.9292 5 5 5 555 555 21176 4335 1 38.675 5 5 5 555 555 15706 4294 1 38.675 5 5 5 555 555 11511 4293 1 38.675 5 5 5 555 555 22841 4301 1 38.675 5 5 5 555 555 12429 4301 1 38.675 5 5 5 555 555 13831 4300 1 38.675 5 5 5 555 555 16582 4312 1 38.675 5 5 5 555 555 21962 4307 1 38.675 5 5 5 555 555 21989 4280 1 38.675 5 5 5 555 555 11574 4291 1 38.664 5 5 5 555 555 11438 4329 1 38.664 5 5 5 555 555 12374 4327

## Creating RFM Segments Variable 

Now we'll create meaningful segments based on the RFM scores:

In [29]:
-- This query creates specific customer segments based on RFM scores
-- It classifies customers into distinct marketing segments
-- Enables targeted marketing strategies based on customer behavior
WITH CustomerRFM AS (
    SELECT 
        c.CustomerID,
        DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency,
        COUNT(DISTINCT soh.SalesOrderID) AS Frequency,
        SUM(soh.TotalDue) AS Monetary
    FROM 
        Sales.Customer c
        JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
    GROUP BY 
        c.CustomerID
),
RFM_Scores AS (
    SELECT 
        CustomerID,
        Recency,
        Frequency,
        Monetary,
        NTILE(5) OVER (ORDER BY Recency ASC) AS R_Score,
        NTILE(5) OVER (ORDER BY Frequency DESC) AS F_Score,
        NTILE(5) OVER (ORDER BY Monetary DESC) AS M_Score
    FROM 
        CustomerRFM
)
SELECT 
    CustomerID,
    Recency,
    Frequency,
    Monetary,
    R_Score,
    F_Score,
    M_Score,
    CAST(R_Score AS VARCHAR) + CAST(F_Score AS VARCHAR) + CAST(M_Score AS VARCHAR) AS RFM_Score,
    CASE
        -- Champions: Recent shoppers who buy often and spend a lot
        WHEN R_Score >= 4 AND F_Score >= 4 AND M_Score >= 4 THEN 'Champions'
        
        -- Loyal Customers: Recent shoppers who buy often
        WHEN R_Score >= 4 AND F_Score >= 4 AND M_Score >= 3 THEN 'Loyal Customers'
        
        -- Potential Loyalists: Recent customers with average frequency
        WHEN R_Score >= 4 AND F_Score >= 3 THEN 'Potential Loyalists'
        
        -- Recent Customers: Recent shoppers who haven't shopped frequently
        WHEN R_Score >= 4 AND F_Score <= 2 THEN 'New Customers'
        
        -- Promising: Recent shoppers who haven't spent much
        WHEN R_Score >= 3 AND F_Score <= 2 AND M_Score <= 2 THEN 'Promising'
        
        -- Need Attention: Above average recency, frequency, and monetary
        WHEN R_Score >= 3 AND F_Score >= 3 AND M_Score >= 3 THEN 'Need Attention'
        
        -- At Risk: Below average recency, above average frequency and monetary
        WHEN R_Score <= 2 AND F_Score >= 3 AND M_Score >= 3 THEN 'At Risk'
        
        -- Can't Lose Them: Spent a lot, purchased often, but long time ago
        WHEN R_Score <= 2 AND F_Score >= 4 AND M_Score >= 4 THEN 'Can''t Lose Them'
        
        -- Hibernating: Last purchase long ago, low spending and frequency
        WHEN R_Score <= 2 AND F_Score <= 2 AND M_Score <= 2 THEN 'Hibernating'
        
        -- Lost: Lowest scores across all metrics
        WHEN R_Score = 1 AND F_Score = 1 AND M_Score = 1 THEN 'Lost'
        
        ELSE 'Other'
    END AS Customer_Segment
FROM 
    RFM_Scores
ORDER BY 
    Customer_Segment;

(19119 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.553

CustomerID Recency Frequency Monetary R_Score F_Score M_Score RFM_Score Customer_Segment 21930 4019 1 1363.5258 1 4 3 143 At Risk 20884 4053 1 1359.1058 2 3 3 233 At Risk 25639 4075 1 1357.8572 2 3 3 233 At Risk 23799 4019 1 1357.8572 1 4 3 143 At Risk 25693 4018 1 1366.6419 1 4 3 143 At Risk 27161 4033 1 1366.6419 1 3 3 133 At Risk 27154 4072 1 1357.8572 2 3 3 233 At Risk 27136 4097 1 1352.3432 2 3 3 233 At Risk 25694 4030 1 1352.3432 1 3 3 133 At Risk 27169 4028 1 1342.4093 1 3 3 133 At Risk 28103 4019 1 1342.4093 1 4 3 143 At Risk 21583 4076 1 1341.9783 2 3 3 233 At Risk 25510 4045 1 1340.3098 2 3 3 233 At Risk 21483 4076 1 1332.0444 2 3 3 233 At Risk 21685 4035 1 1332.0444 1 3 3 133 At Risk 21723 4039 1 1332.0444 1 3 3 133 At Risk 21728 4061 1 1332.0444 2 3 3 233 At Risk 21357 4093 1 1332.0444 2 3 3 233 At Risk 22152 4024 1 1332.0444 1 4 3 143 At Risk 21926 4023 1 1324.8619 1 4 3 143 At Risk 25312 4052 1 1324.8619 2 3 3 233 At Risk 28563 4084 1 1323.7569 2 3 3 233 At Risk 28522 4097 1 1323.7569 2 3 3 233 At Risk 24138 4070 1 1320.4419 2 3 3 233 At Risk 21436 4005 1 1319.3148 1 4 3 143 At Risk 28702 4043 1 1318.7623 2 3 3 233 At Risk 21476 4069 1 1323.1381 2 3 3 233 At Risk 25585 4005 1 1313.2483 1 4 3 143 At Risk 22245 4023 1 1313.2483 1 4 3 143 At Risk 25531 4058 1 1313.2483 2 3 3 233 At Risk 27590 4008 1 1314.3533 1 4 3 143 At Risk 21422 4059 1 1308.8283 2 3 3 233 At Risk 21920 4037 1 1308.8283 1 3 3 133 At Risk 22137 4026 1 1308.8283 1 3 3 133 At Risk 21355 4091 1 1308.8283 2 3 3 233 At Risk 27694 4013 1 1308.8283 1 4 3 143 At Risk 27696 4024 1 1307.7344 1 4 3 143 At Risk 21434 4005 1 1307.7344 1 4 3 143 At Risk 27687 4009 1 1307.7344 1 4 3 143 At Risk 21929 4026 1 1307.7344 1 3 3 133 At Risk 27589 4030 1 1307.7344 1 3 3 133 At Risk 21645 4049 1 1307.7344 2 3 3 233 At Risk 21100 4020 1 1302.1873 1 4 3 143 At Risk 25636 4021 1 1297.8004 1 4 3 143 At Risk 21910 4017 1 1297.8004 1 4 3 143 At Risk 21429 4013 1 1297.8004 1 4 3 143 At Risk 25599 4020 1 1297.8004 1 4 3 143 At Risk 22253 4003 1 1297.8004 1 4 3 143 At Risk 22318 4005 1 1297.8004 1 4 3 143 At Risk 27712 4005 1 1297.8004 1 4 3 143 At Risk 22186 4008 1 1297.8004 1 4 3 143 At Risk 25604 4014 1 1297.8004 1 4 3 143 At Risk 25502 4016 1 1297.8004 1 4 3 143 At Risk 22391 4015 1 1297.8004 1 4 3 143 At Risk 21781 4057 1 1297.8004 2 3 3 233 At Risk 21588 4051 1 1297.8004 2 3 3 233 At Risk 24702 4059 1 1297.8004 2 3 3 233 At Risk 20888 4047 1 1297.8004 2 3 3 233 At Risk 21798 4050 1 1297.8004 2 3 3 233 At Risk 25448 4042 1 1297.8004 1 3 3 133 At Risk 21941 4030 1 1297.8004 1 3 3 133 At Risk 22111 4030 1 1297.8004 1 3 3 133 At Risk 21746 4040 1 1297.8004 1 3 3 133 At Risk 21401 4079 1 1297.8004 2 3 3 233 At Risk 21491 4079 1 1297.8004 2 3 3 233 At Risk 28564 4033 1 1297.8004 1 3 3 133 At Risk 21356 4068 1 1297.8004 2 3 3 233 At Risk 21700 4062 1 1297.8004 2 3 3 233 At Risk 21604 4047 1 1303.8669 2 3 3 233 At Risk 21711 4056 1 1303.8669 2 3 3 233 At Risk 21794 4060 1 1303.8669 2 3 3 233 At Risk 21585 4066 1 1303.8669 2 3 3 233 At Risk 22188 4011 1 1303.8669 1 4 3 143 At Risk 22220 4005 1 1303.8669 1 4 3 143 At Risk 22236 4004 1 1303.8669 1 4 3 143 At Risk 27698 4023 1 1303.8669 1 4 3 143 At Risk 21147 4098 1 1303.8669 2 3 3 233 At Risk 25546 4063 1 1303.3144 2 3 3 233 At Risk 21329 4081 1 1303.3144 2 3 3 233 At Risk 21388 4077 1 1303.3144 2 3 3 233 At Risk 21605 4057 1 1303.3144 2 3 3 233 At Risk 21161 4100 1 1297.8004 2 3 3 233 At Risk 25301 4070 1 1293.3804 2 3 3 233 At Risk 28700 4063 1 1293.3804 2 3 3 233 At Risk 21424 4083 1 1293.3804 2 3 3 233 At Risk 24697 4084 1 1293.3804 2 3 3 233 At Risk 24211 4077 1 1293.3804 2 3 3 233 At Risk 21396 4090 1 1293.3804 2 3 3 233 At Risk 22246 4029 1 1293.3804 1 3 3 133 At Risk 21643 4036 1 1293.3804 1 3 3 133 At Risk 25576 4049 1 1293.3804 2 3 3 233 At Risk 22243 4027 1 1293.3804 1 3 3 133 At Risk 25500 4044 1 1293.3804 2 3 3 233 At Risk 20882 4049 1 1293.3804 2 3 3 233 At Risk 24835 4051 1 1293.3804 2 3 3 233 At Risk 21599 4056 1 129

## Revenue Analysis by Segment

Now, let's examine the revenue contribution of each segment:

In [30]:
-- This query analyzes revenue contribution by RFM segment
-- Shows which segments drive the most revenue
-- Helps identify high-value segments for retention focus
WITH CustomerRFM AS (
    SELECT 
        c.CustomerID,
        DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency,
        COUNT(DISTINCT soh.SalesOrderID) AS Frequency,
        SUM(soh.TotalDue) AS Monetary
    FROM 
        Sales.Customer c
        JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
    GROUP BY 
        c.CustomerID
),
RFM_Scores AS (
    SELECT 
        CustomerID,
        Recency,
        Frequency,
        Monetary,
        NTILE(5) OVER (ORDER BY Recency ASC) AS R_Score,
        NTILE(5) OVER (ORDER BY Frequency DESC) AS F_Score,
        NTILE(5) OVER (ORDER BY Monetary DESC) AS M_Score
    FROM 
        CustomerRFM
),
RFM_Segments AS (
    SELECT 
        CustomerID,
        Monetary,
        CASE
            WHEN R_Score >= 4 AND F_Score >= 4 AND M_Score >= 4 THEN 'Champions'
            WHEN R_Score >= 4 AND F_Score >= 4 AND M_Score >= 3 THEN 'Loyal Customers'
            WHEN R_Score >= 4 AND F_Score >= 3 THEN 'Potential Loyalists'
            WHEN R_Score >= 4 AND F_Score <= 2 THEN 'New Customers'
            WHEN R_Score >= 3 AND F_Score <= 2 AND M_Score <= 2 THEN 'Promising'
            WHEN R_Score >= 3 AND F_Score >= 3 AND M_Score >= 3 THEN 'Need Attention'
            WHEN R_Score <= 2 AND F_Score >= 3 AND M_Score >= 3 THEN 'At Risk'
            WHEN R_Score <= 2 AND F_Score >= 4 AND M_Score >= 4 THEN 'Can''t Lose Them'
            WHEN R_Score <= 2 AND F_Score <= 2 AND M_Score <= 2 THEN 'Hibernating'
            WHEN R_Score = 1 AND F_Score = 1 AND M_Score = 1 THEN 'Lost'
            ELSE 'Other'
        END AS Customer_Segment
    FROM 
        RFM_Scores
)
SELECT 
    Customer_Segment,
    COUNT(*) AS Customer_Count,
    SUM(Monetary) AS Total_Revenue,
    CAST(SUM(Monetary) * 100.0 / (SELECT SUM(Monetary) FROM RFM_Segments) AS DECIMAL(5,2)) AS Revenue_Percentage,
    AVG(Monetary) AS Average_Revenue_Per_Customer
FROM 
    RFM_Segments
GROUP BY 
    Customer_Segment
ORDER BY 
    Total_Revenue DESC;

(9 rows affected)

Total execution time: 00:00:00.221

Customer_Segment Customer_Count Total_Revenue Revenue_Percentage Average_Revenue_Per_Customer Hibernating 2432 85474670.187 69.37 35145.8347 New Customers 2279 23710953.8105 19.24 10404.1043 Promising 1229 6350180.0172 5.15 5166.9487 Potential Loyalists 1124 3090259.7721 2.51 2749.3414 Other 2612 2397749.5262 1.95 917.9745 Loyal Customers 1245 848368.0239 0.69 681.42 At Risk 3344 788022.6787 0.64 235.6527 Need Attention 1855 417755.3402 0.34 225.205 Champions 2999 138826.7601 0.11 46.291

## Territory Distribution by Segment

Let's analyze how different segments are distributed across territories

In [31]:
-- This query analyzes segment distribution across territories
-- Shows geographic patterns in customer segments
-- Helps develop region-specific marketing strategies
WITH CustomerRFM AS (
    SELECT 
        c.CustomerID,
        st.TerritoryID,
        st.Name AS Territory,
        DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency,
        COUNT(DISTINCT soh.SalesOrderID) AS Frequency,
        SUM(soh.TotalDue) AS Monetary
    FROM 
        Sales.Customer c
        JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
        JOIN Sales.SalesTerritory st ON soh.TerritoryID = st.TerritoryID
    GROUP BY 
        c.CustomerID, st.TerritoryID, st.Name
),
RFM_Scores AS (
    SELECT 
        CustomerID,
        Territory,
        Recency,
        Frequency,
        Monetary,
        NTILE(5) OVER (ORDER BY Recency ASC) AS R_Score,
        NTILE(5) OVER (ORDER BY Frequency DESC) AS F_Score,
        NTILE(5) OVER (ORDER BY Monetary DESC) AS M_Score
    FROM 
        CustomerRFM
),
RFM_Segments AS (
    SELECT 
        CustomerID,
        Territory,
        CASE
            WHEN R_Score >= 4 AND F_Score >= 4 AND M_Score >= 4 THEN 'Champions'
            WHEN R_Score >= 4 AND F_Score >= 4 AND M_Score >= 3 THEN 'Loyal Customers'
            WHEN R_Score >= 4 AND F_Score >= 3 THEN 'Potential Loyalists'
            WHEN R_Score >= 4 AND F_Score <= 2 THEN 'New Customers'
            WHEN R_Score >= 3 AND F_Score <= 2 AND M_Score <= 2 THEN 'Promising'
            WHEN R_Score >= 3 AND F_Score >= 3 AND M_Score >= 3 THEN 'Need Attention'
            WHEN R_Score <= 2 AND F_Score >= 3 AND M_Score >= 3 THEN 'At Risk'
            WHEN R_Score <= 2 AND F_Score >= 4 AND M_Score >= 4 THEN 'Can''t Lose Them'
            WHEN R_Score <= 2 AND F_Score <= 2 AND M_Score <= 2 THEN 'Hibernating'
            WHEN R_Score = 1 AND F_Score = 1 AND M_Score = 1 THEN 'Lost'
            ELSE 'Other'
        END AS Customer_Segment
    FROM 
        RFM_Scores
)
SELECT 
    Territory,
    Customer_Segment,
    COUNT(*) AS Customer_Count,
    CAST(COUNT(*) * 100.0 / (SELECT COUNT(*) FROM RFM_Segments WHERE Territory = rs.Territory) AS DECIMAL(5,2)) AS Percentage_Within_Territory
FROM 
    RFM_Segments rs
GROUP BY 
    Territory, Customer_Segment
ORDER BY 
    Territory, Customer_Count DESC;

(88 rows affected)

Total execution time: 00:00:00.265

Territory Customer_Segment Customer_Count Percentage_Within_Territory Australia Hibernating 813 22.43 Australia New Customers 790 21.79 Australia Other 600 16.55 Australia Promising 446 12.30 Australia At Risk 315 8.69 Australia Champions 307 8.47 Australia Need Attention 193 5.32 Australia Loyal Customers 93 2.57 Australia Potential Loyalists 68 1.88 Canada Other 504 30.05 Canada At Risk 192 11.45 Canada Hibernating 190 11.33 Canada Champions 185 11.03 Canada New Customers 175 10.44 Canada Potential Loyalists 142 8.47 Canada Loyal Customers 118 7.04 Canada Need Attention 107 6.38 Canada Promising 64 3.82 Central Hibernating 36 52.17 Central New Customers 22 31.88 Central Champions 3 4.35 Central At Risk 2 2.90 Central Loyal Customers 2 2.90 Central Potential Loyalists 1 1.45 Central Promising 1 1.45 Central Need Attention 1 1.45 Central Other 1 1.45 France At Risk 415 22.51 France Champions 394 21.37 France Hibernating 233 12.64 France Need Attention 233 12.64 France New Customers 150 8.13 France Loyal Customers 127 6.89 France Other 103 5.59 France Promising 101 5.48 France Potential Loyalists 88 4.77 Germany At Risk 413 22.79 Germany Champions 354 19.54 Germany Hibernating 262 14.46 Germany Need Attention 222 12.25 Germany New Customers 151 8.33 Germany Loyal Customers 121 6.68 Germany Promising 112 6.18 Germany Other 94 5.19 Germany Potential Loyalists 83 4.58 Northeast Hibernating 36 63.16 Northeast New Customers 10 17.54 Northeast Champions 3 5.26 Northeast Other 3 5.26 Northeast At Risk 2 3.51 Northeast Potential Loyalists 2 3.51 Northeast Promising 1 1.75 Northwest At Risk 780 22.75 Northwest Champions 692 20.19 Northwest Other 407 11.87 Northwest Need Attention 401 11.70 Northwest New Customers 293 8.55 Northwest Potential Loyalists 259 7.56 Northwest Loyal Customers 238 6.94 Northwest Hibernating 200 5.83 Northwest Promising 158 4.61 Southeast Hibernating 46 50.55 Southeast New Customers 25 27.47 Southeast Other 5 5.49 Southeast Loyal Customers 4 4.40 Southeast At Risk 3 3.30 Southeast Champions 3 3.30 Southeast Need Attention 2 2.20 Southeast Potential Loyalists 2 2.20 Southeast Promising 1 1.10 Southwest At Risk 929 20.35 Southwest Champions 824 18.05 Southwest Other 550 12.05 Southwest Need Attention 516 11.30 Southwest Potential Loyalists 412 9.03 Southwest New Customers 407 8.92 Southwest Loyal Customers 372 8.15 Southwest Hibernating 331 7.25 Southwest Promising 224 4.91 United Kingdom Other 340 17.43 United Kingdom At Risk 292 14.97 United Kingdom Hibernating 288 14.76 United Kingdom New Customers 257 13.17 United Kingdom Champions 235 12.05 United Kingdom Need Attention 183 9.38 United Kingdom Loyal Customers 169 8.66 United Kingdom Promising 121 6.20 United Kingdom Potential Loyalists 66 3.38

## Product Category Preferences by Segment

Let's analyze which product categories are preferred by each customer segment:

In [32]:
-- This query analyzes product category preferences by RFM segment
-- Shows which products are popular with each customer segment
-- Enables targeted product recommendations and promotions
WITH CustomerRFM AS (
    SELECT 
        c.CustomerID,
        DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency,
        COUNT(DISTINCT soh.SalesOrderID) AS Frequency,
        SUM(soh.TotalDue) AS Monetary
    FROM 
        Sales.Customer c
        JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
    GROUP BY 
        c.CustomerID
),
RFM_Scores AS (
    SELECT 
        CustomerID,
        Recency,
        Frequency,
        Monetary,
        NTILE(5) OVER (ORDER BY Recency ASC) AS R_Score,
        NTILE(5) OVER (ORDER BY Frequency DESC) AS F_Score,
        NTILE(5) OVER (ORDER BY Monetary DESC) AS M_Score
    FROM 
        CustomerRFM
),
RFM_Segments AS (
    SELECT 
        CustomerID,
        CASE
            WHEN R_Score >= 4 AND F_Score >= 4 AND M_Score >= 4 THEN 'Champions'
            WHEN R_Score >= 4 AND F_Score >= 4 AND M_Score >= 3 THEN 'Loyal Customers'
            WHEN R_Score >= 4 AND F_Score >= 3 THEN 'Potential Loyalists'
            WHEN R_Score >= 4 AND F_Score <= 2 THEN 'New Customers'
            WHEN R_Score >= 3 AND F_Score <= 2 AND M_Score <= 2 THEN 'Promising'
            WHEN R_Score >= 3 AND F_Score >= 3 AND M_Score >= 3 THEN 'Need Attention'
            WHEN R_Score <= 2 AND F_Score >= 3 AND M_Score >= 3 THEN 'At Risk'
            WHEN R_Score <= 2 AND F_Score >= 4 AND M_Score >= 4 THEN 'Can''t Lose Them'
            WHEN R_Score <= 2 AND F_Score <= 2 AND M_Score <= 2 THEN 'Hibernating'
            WHEN R_Score = 1 AND F_Score = 1 AND M_Score = 1 THEN 'Lost'
            ELSE 'Other'
        END AS Customer_Segment
    FROM 
        RFM_Scores
)
SELECT 
    rs.Customer_Segment,
    pc.Name AS Product_Category,
    COUNT(DISTINCT sod.SalesOrderID) AS Order_Count,
    SUM(sod.LineTotal) AS Total_Revenue,
    CAST(SUM(sod.LineTotal) * 100.0 / 
        (SELECT SUM(sod2.LineTotal) 
         FROM Sales.SalesOrderDetail sod2 
         JOIN Sales.SalesOrderHeader soh2 ON sod2.SalesOrderID = soh2.SalesOrderID
         JOIN RFM_Segments rs2 ON soh2.CustomerID = rs2.CustomerID
         WHERE rs2.Customer_Segment = rs.Customer_Segment) 
    AS DECIMAL(5,2)) AS Percentage_Of_Segment_Revenue,
    AVG(sod.OrderQty) AS Avg_Quantity_Per_Order
FROM 
    RFM_Segments rs
    JOIN Sales.SalesOrderHeader soh ON rs.CustomerID = soh.CustomerID
    JOIN Sales.SalesOrderDetail sod ON soh.SalesOrderID = sod.SalesOrderID
    JOIN Production.Product p ON sod.ProductID = p.ProductID
    JOIN Production.ProductSubcategory psc ON p.ProductSubcategoryID = psc.ProductSubcategoryID
    JOIN Production.ProductCategory pc ON psc.ProductCategoryID = pc.ProductCategoryID
GROUP BY 
    rs.Customer_Segment, pc.Name
ORDER BY 
    Total_Revenue DESC;

(33 rows affected)

Total execution time: 00:00:04.541

Customer_Segment Product_Category Order_Count Total_Revenue Percentage_Of_Segment_Revenue Avg_Quantity_Per_Order Hibernating Bikes 7119 63500993.886741 83.59 2 New Customers Bikes 4396 19277818.665890 91.01 1 Hibernating Components 2205 10247076.362811 13.49 2 Promising Bikes 2727 5664020.179800 98.64 1 Potential Loyalists Bikes 1124 2767410.556900 98.96 1 Other Bikes 946 1903771.527800 87.74 1 Hibernating Clothing 2887 1616113.969943 2.13 4 New Customers Components 396 1536601.492919 7.25 2 Loyal Customers Bikes 918 691065.519600 90.02 1 Hibernating Accessories 3223 606144.253281 0.80 3 At Risk Bikes 738 555148.164000 77.85 1 Need Attention Bikes 400 290944.204000 76.96 1 New Customers Clothing 1278 240703.704758 1.14 3 Other Accessories 4356 183956.956000 8.48 1 New Customers Accessories 2258 128109.953145 0.60 1 At Risk Accessories 2852 102417.920000 14.36 1 Champions Accessories 2751 88080.264000 70.11 1 Other Clothing 1780 80014.822000 3.69 1 Need Attention Accessories 1629 58190.080000 15.39 1 At Risk Clothing 1141 55248.272000 7.75 1 Loyal Customers Accessories 826 43208.490000 5.63 1 Promising Accessories 1137 43095.397500 0.75 1 Champions Clothing 880 37459.696800 29.82 1 Loyal Customers Clothing 522 30924.790000 4.03 1 Need Attention Clothing 622 28918.650000 7.65 1 Promising Clothing 519 21062.489300 0.37 1 Potential Loyalists Accessories 492 18869.570000 0.67 1 Promising Components 23 14050.488400 0.24 1 Potential Loyalists Clothing 248 10096.130000 0.36 1 Loyal Customers Components 10 2451.227100 0.32 1 Other Components 13 2013.578200 0.09 1 At Risk Components 1 308.304000 0.04 1 Champions Components 2 91.833000 0.07 1

##  Segment-Specific Marketing Recommendations

Based on our RFM analysis, here are segment-specific marketing recommendations:

## **Top Customer from Champions**

In [33]:
-- Example query to identify Champions segment customers
-- These are your best customers who shop regularly and spend a lot
SELECT TOP 10
    c.CustomerID,
    p.FirstName + ' ' + p.LastName AS CustomerName,
    st.Name AS Territory,
    crfm.Recency AS DaysSinceLastPurchase,
    crfm.Frequency AS PurchaseCount,
    crfm.Monetary AS TotalSpend,
    crfm.LastPurchaseDate
FROM 
    Sales.Customer c
    JOIN Person.Person p ON c.PersonID = p.BusinessEntityID
    JOIN Sales.SalesTerritory st ON c.TerritoryID = st.TerritoryID
    JOIN (
        SELECT 
            c.CustomerID,
            DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency,
            COUNT(DISTINCT soh.SalesOrderID) AS Frequency,
            SUM(soh.TotalDue) AS Monetary,
            MAX(soh.OrderDate) AS LastPurchaseDate
        FROM 
            Sales.Customer c
            JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
        GROUP BY 
            c.CustomerID
    ) crfm ON c.CustomerID = crfm.CustomerID
WHERE 
    -- Find customers with low recency (recent purchases, below 20th percentile)
    crfm.Recency <= (
        SELECT 
            MAX(Recency) AS RecencyThreshold
        FROM (
            SELECT 
                DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency,
                NTILE(5) OVER (ORDER BY DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE()))) AS RecencyQuintile
            FROM 
                Sales.Customer c
                JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
            GROUP BY 
                c.CustomerID
        ) AS RecencyStats
        WHERE RecencyQuintile = 5 -- Top quintile (5 is best for recency when using NTILE)
    )
    -- Find customers with high frequency (above 80th percentile)
    AND crfm.Frequency >= (
        SELECT 
            MIN(Frequency) AS FrequencyThreshold
        FROM (
            SELECT 
                COUNT(DISTINCT soh.SalesOrderID) AS Frequency,
                NTILE(5) OVER (ORDER BY COUNT(DISTINCT soh.SalesOrderID) DESC) AS FrequencyQuintile
            FROM 
                Sales.Customer c
                JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
            GROUP BY 
                c.CustomerID
        ) AS FrequencyStats
        WHERE FrequencyQuintile = 1 -- Top quintile (1 is best for frequency when using NTILE with DESC)
    )
    -- Find customers with high monetary value (above 80th percentile)
    AND crfm.Monetary >= (
        SELECT 
            MIN(Monetary) AS MonetaryThreshold
        FROM (
            SELECT 
                SUM(soh.TotalDue) AS Monetary,
                NTILE(5) OVER (ORDER BY SUM(soh.TotalDue) DESC) AS MonetaryQuintile
            FROM 
                Sales.Customer c
                JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID
            GROUP BY 
                c.CustomerID
        ) AS MonetaryStats
        WHERE MonetaryQuintile = 1 -- Top quintile (1 is best for monetary when using NTILE with DESC)
    )
ORDER BY 
    crfm.Monetary DESC;

(10 rows affected)

Total execution time: 00:00:00.414

CustomerID CustomerName Territory DaysSinceLastPurchase PurchaseCount TotalSpend LastPurchaseDate 29818 Roger Harui Northwest 4063 12 989184.082 2014-03-31 00:00:00.000 29715 Andrew Dixon Southeast 4032 12 961675.8596 2014-05-01 00:00:00.000 29722 Reuben D'sa Canada 4032 12 954021.9235 2014-05-01 00:00:00.000 30117 Robert Vessa Southwest 4063 12 919801.8188 2014-03-31 00:00:00.000 29614 Ryan Calafato Canada 4093 12 901346.856 2014-03-01 00:00:00.000 29639 Joseph Castellucio Canada 4032 12 887090.4106 2014-05-01 00:00:00.000 29701 Kirk DeGrasse Northeast 4032 8 841866.5522 2014-05-01 00:00:00.000 29617 Lindsey Camacho Northwest 4063 12 834475.9271 2014-03-31 00:00:00.000 29994 Robin McGuigan Canada 4093 12 824331.7682 2014-03-01 00:00:00.000 29646 Stacey Cereghino Southwest 4093 12 820383.5466 2014-03-01 00:00:00.000

**Recommendations for Champions:**

1. **Loyalty Programs:** Offer exclusive loyalty rewards and early access to new products
2. **VIP Services:** Provide personalized shopping experiences and premium customer service
3. **Ambassador Programs:** Invite them to become brand ambassadors
4. **Premium Product Focus:** Showcase high-end products and premium options
5. **Recognition:** Send thank-you notes, exclusive gifts, and recognition for their loyalty

## **Top At Risk Customers**

In [34]:
-- This query correctly identifies At Risk customers
SELECT TOP 10 
    c.CustomerID, 
    p.FirstName + ' ' + p.LastName AS CustomerName, 
    st.Name AS Territory, 
    crfm.Recency AS DaysSinceLastPurchase, 
    crfm.Frequency AS PurchaseCount, 
    crfm.Monetary AS TotalSpend, 
    crfm.LastPurchaseDate,
    crfm.R_Score,
    crfm.F_Score,
    crfm.M_Score
FROM 
    Sales.Customer c 
    JOIN Person.Person p ON c.PersonID = p.BusinessEntityID 
    JOIN Sales.SalesTerritory st ON c.TerritoryID = st.TerritoryID 
    JOIN (
        SELECT 
            c.CustomerID, 
            DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency, 
            COUNT(DISTINCT soh.SalesOrderID) AS Frequency, 
            SUM(soh.TotalDue) AS Monetary, 
            MAX(soh.OrderDate) AS LastPurchaseDate,
            NTILE(5) OVER (ORDER BY DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) ASC) AS R_Score,
            NTILE(5) OVER (ORDER BY COUNT(DISTINCT soh.SalesOrderID) DESC) AS F_Score,
            NTILE(5) OVER (ORDER BY SUM(soh.TotalDue) DESC) AS M_Score
        FROM 
            Sales.Customer c 
            JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID 
        GROUP BY 
            c.CustomerID
    ) crfm ON c.CustomerID = crfm.CustomerID 
WHERE 
    crfm.R_Score <= 2  -- Low recency score (hasn't purchased recently)
    AND crfm.F_Score >= 3  -- Higher frequency score
    AND crfm.M_Score >= 3  -- Higher monetary score
ORDER BY 
    crfm.Recency DESC;

(10 rows affected)

Total execution time: 00:00:00.393

CustomerID CustomerName Territory DaysSinceLastPurchase PurchaseCount TotalSpend LastPurchaseDate R_Score F_Score M_Score 20486 Jack Butler Southwest 4101 1 55.2169 2014-02-21 00:00:00.000 2 3 4 22965 Carrie Gomez Australia 4101 1 8.0444 2014-02-21 00:00:00.000 2 3 5 27642 Kayla Johnson Southwest 4101 1 33.6804 2014-02-21 00:00:00.000 2 3 5 22902 Pedro Madan Northwest 4101 1 35.6694 2014-02-21 00:00:00.000 2 3 5 23391 Joanna Moreno Southwest 4101 1 677.8623 2014-02-21 00:00:00.000 2 3 3 21101 Meagan Perez United Kingdom 4101 1 35.6694 2014-02-21 00:00:00.000 2 3 5 23403 Justin Powell Northwest 4101 1 612.1369 2014-02-21 00:00:00.000 2 3 3 24843 Bryant Subram Germany 4101 1 98.3229 2014-02-21 00:00:00.000 2 3 4 25089 Christy Xie Northwest 4101 1 38.5535 2014-02-21 00:00:00.000 2 3 5 23169 Corey Andersen Northwest 4100 1 757.4444 2014-02-22 00:00:00.000 2 3 3

**Recommendations for At Risk Customers:**

1. **Reactivation Campaigns:** Send targeted win-back emails with personalized offers
2. **Special Discounts:** Offer special "we miss you" discounts
3. **Feedback Surveys:** Ask for feedback on what might have gone wrong
4. **New Product Announcements:** Highlight new products relevant to their purchase history
5. **Multichannel Approach:** Use multiple channels (email, SMS, direct mail) to re-engage

## **Top Loyal Customers**

In [38]:
-- Identifies Velocity Riders (Loyal Customers) segment
-- Recent and frequent shoppers with good spending levels
SELECT TOP 10 
    c.CustomerID, 
    p.FirstName + ' ' + p.LastName AS CustomerName, 
    st.Name AS Territory, 
    crfm.Recency AS DaysSinceLastPurchase, 
    crfm.Frequency AS PurchaseCount, 
    crfm.Monetary AS TotalSpend, 
    crfm.LastPurchaseDate
FROM 
    Sales.Customer c 
    JOIN Person.Person p ON c.PersonID = p.BusinessEntityID 
    JOIN Sales.SalesTerritory st ON c.TerritoryID = st.TerritoryID 
    JOIN (
        SELECT 
            c.CustomerID, 
            DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency, 
            COUNT(DISTINCT soh.SalesOrderID) AS Frequency, 
            SUM(soh.TotalDue) AS Monetary, 
            MAX(soh.OrderDate) AS LastPurchaseDate,
            NTILE(5) OVER (ORDER BY DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) ASC) AS R_Score,
            NTILE(5) OVER (ORDER BY COUNT(DISTINCT soh.SalesOrderID) DESC) AS F_Score,
            NTILE(5) OVER (ORDER BY SUM(soh.TotalDue) DESC) AS M_Score
        FROM 
            Sales.Customer c 
            JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID 
        GROUP BY 
            c.CustomerID
    ) crfm ON c.CustomerID = crfm.CustomerID 
WHERE 
    crfm.R_Score >= 4  -- High recency score (recent purchases)
    AND crfm.F_Score >= 4  -- High frequency score (frequent purchases)
    AND crfm.M_Score >= 3  -- Good monetary score (decent spend levels)
    AND crfm.M_Score < 4   -- But not highest spenders
ORDER BY 
    crfm.Frequency DESC;

(10 rows affected)

Total execution time: 00:00:00.461

CustomerID CustomerName Territory DaysSinceLastPurchase PurchaseCount TotalSpend LastPurchaseDate 26826 Kendra Romero Germany 4366 1 1367.7911 2013-06-01 00:00:00.000 25096 Victoria Bennett Northwest 4322 1 1366.6419 2013-07-15 00:00:00.000 23774 Reginald Harrison United Kingdom 4270 1 1364.0673 2013-09-05 00:00:00.000 25538 Andy Jiménez France 4280 1 1357.8572 2013-08-26 00:00:00.000 25381 Dylan Li Southwest 4263 1 1357.8572 2013-09-12 00:00:00.000 25383 Nathan Walker Northwest 4265 1 1357.8572 2013-09-10 00:00:00.000 25413 Zoe Rivera Northwest 4188 1 1357.8572 2013-11-26 00:00:00.000 25085 Lucas Rogers Southwest 4345 1 1357.8572 2013-06-22 00:00:00.000 26825 Jamie Jimenez Germany 4338 1 1357.8572 2013-06-29 00:00:00.000 29401 Jésus Gomez United Kingdom 4343 1 1352.3432 2013-06-24 00:00:00.000

**Recommendations for Loyal Customers:**

1. **Anniversary Milestone Rewards:** Create personalized "loyalty milestones" with escalating rewards based on their specific purchase anniversary dates
2. **Product Input Privileges:** Develop a "Product Insider" program where loyal customers can influence upcoming product development and get first access
3. **Personalized Subscription Bundles:** Offer custom-created product bundles based on their purchase history with convenient auto-delivery options
4. **Tier-Jumping Challenges:** Create gamified "challenges" that allow loyal customers to accelerate their status to the next loyalty tier through targeted behaviors
5. **Dedicated Personal Shopper:** Assign a specific team member who proactively reaches out with personalized recommendations before seasonal events or holidays

## **Top Potential Loyalists**

In [41]:

SELECT TOP 10 
    c.CustomerID, 
    p.FirstName + ' ' + p.LastName AS CustomerName, 
    st.Name AS Territory, 
    crfm.Recency AS DaysSinceLastPurchase, 
    crfm.Frequency AS PurchaseCount, 
    crfm.Monetary AS TotalSpend, 
    crfm.LastPurchaseDate
FROM 
    Sales.Customer c 
    JOIN Person.Person p ON c.PersonID = p.BusinessEntityID 
    JOIN Sales.SalesTerritory st ON c.TerritoryID = st.TerritoryID 
    JOIN (
        SELECT 
            c.CustomerID, 
            DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency, 
            COUNT(DISTINCT soh.SalesOrderID) AS Frequency, 
            SUM(soh.TotalDue) AS Monetary, 
            MAX(soh.OrderDate) AS LastPurchaseDate,
            NTILE(5) OVER (ORDER BY DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) ASC) AS R_Score,
            NTILE(5) OVER (ORDER BY COUNT(DISTINCT soh.SalesOrderID) DESC) AS F_Score,
            NTILE(5) OVER (ORDER BY SUM(soh.TotalDue) DESC) AS M_Score
        FROM 
            Sales.Customer c 
            JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID 
        GROUP BY 
            c.CustomerID
    ) crfm ON c.CustomerID = crfm.CustomerID 
WHERE 
    crfm.R_Score >= 3  -- Modified: Moderately recent purchases (was 4)
    AND crfm.F_Score >= 3  -- Moderate frequency score
    AND crfm.F_Score < 5   -- Modified: Not the highest frequency (was < 4)
    -- Added condition to differentiate from other segments
    AND NOT (crfm.R_Score >= 4 AND crfm.F_Score >= 4) -- Exclude Loyal Customers & Champions
ORDER BY 
    crfm.R_Score DESC, crfm.F_Score DESC;

(10 rows affected)

Total execution time: 00:00:00.186

CustomerID CustomerName Territory DaysSinceLastPurchase PurchaseCount TotalSpend LastPurchaseDate 24196 Armando Gill France 4166 1 44.1779 2013-12-18 00:00:00.000 23286 Taylor Bell Southwest 4167 1 33.139 2013-12-17 00:00:00.000 25633 Tara Sutton Germany 4167 1 122.0583 2013-12-17 00:00:00.000 13379 Bailey Morris Northwest 4167 1 26.8184 2013-12-17 00:00:00.000 24514 Jesse Phillips Southwest 4166 1 40.432 2013-12-18 00:00:00.000 27007 Joe Gonzalez United Kingdom 4166 1 125.9258 2013-12-18 00:00:00.000 22719 Jesse Brooks Southwest 4166 1 627.3748 2013-12-18 00:00:00.000 27230 Hunter Wilson Canada 4166 1 15.4479 2013-12-18 00:00:00.000 18471 Paige Stewart Northwest 4166 1 596.689 2013-12-18 00:00:00.000 26969 Cedric Hu Germany 4166 1 26.2769 2013-12-18 00:00:00.000

**Recommendations for Potential Loyalists:**

1. **Interactive Product Journey Maps:** Create personalized visual roadmaps showing how their current purchases connect to future product exploration pathways
2. **Graduated Trial System:** Offer progressively enhanced samples or trial versions of complementary products with each subsequent purchase
3. **Category Completion Badges:** Develop a gamified system where exploring different product categories earns visible status indicators and unlocks special benefits
4. **Value-Stack Demonstrations:** Show clear visualizations of how loyalty program value compounds over time with continued engagement
5. **Micro-community Inclusion:** Connect potential loyalists with existing brand advocates in micro-communities centered around their specific interests or purchase categories

## **Top New Customers**

In [43]:
-- Identifies New Customers segment
-- Recent customers with low purchase frequency
SELECT TOP 10 
    c.CustomerID, 
    p.FirstName + ' ' + p.LastName AS CustomerName, 
    st.Name AS Territory, 
    crfm.Recency AS DaysSinceLastPurchase, 
    crfm.Frequency AS PurchaseCount, 
    crfm.Monetary AS TotalSpend, 
    crfm.LastPurchaseDate
FROM 
    Sales.Customer c 
    JOIN Person.Person p ON c.PersonID = p.BusinessEntityID 
    JOIN Sales.SalesTerritory st ON c.TerritoryID = st.TerritoryID 
    JOIN (
        SELECT 
            c.CustomerID, 
            DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency, 
            COUNT(DISTINCT soh.SalesOrderID) AS Frequency, 
            SUM(soh.TotalDue) AS Monetary, 
            MAX(soh.OrderDate) AS LastPurchaseDate,
            NTILE(5) OVER (ORDER BY DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) ASC) AS R_Score,
            NTILE(5) OVER (ORDER BY COUNT(DISTINCT soh.SalesOrderID) DESC) AS F_Score,
            NTILE(5) OVER (ORDER BY SUM(soh.TotalDue) DESC) AS M_Score
        FROM 
            Sales.Customer c 
            JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID 
        GROUP BY 
            c.CustomerID
    ) crfm ON c.CustomerID = crfm.CustomerID 
WHERE 
    crfm.R_Score >= 4  -- High recency score (recent purchases)
    AND crfm.F_Score <= 2  -- Low frequency score (few purchases)
ORDER BY 
    crfm.Recency ASC, crfm.LastPurchaseDate DESC;

(10 rows affected)

Total execution time: 00:00:00.417

CustomerID CustomerName Territory DaysSinceLastPurchase PurchaseCount TotalSpend LastPurchaseDate 20448 Jésus Blanco Australia 4176 2 6679.272 2013-12-08 00:00:00.000 25865 Tristan Butler Northwest 4176 2 5131.4322 2013-12-08 00:00:00.000 14452 Alex Gonzalez Northwest 4176 2 3732.0242 2013-12-08 00:00:00.000 12179 Alexis Jones Northwest 4176 2 6534.1303 2013-12-08 00:00:00.000 11899 Brenda Perez Australia 4176 3 9049.3976 2013-12-08 00:00:00.000 12108 James Walker Northwest 4176 2 6570.5511 2013-12-08 00:00:00.000 15100 Brenda Chandra Germany 4177 3 7682.6037 2013-12-07 00:00:00.000 11734 Omar Chen Southwest 4177 2 150.037 2013-12-07 00:00:00.000 12057 Madeline Collins Northwest 4177 2 96.4445 2013-12-07 00:00:00.000 23324 Deborah Deng Australia 4177 2 3017.2495 2013-12-07 00:00:00.000

**Recommendations for New Customers:**

1. **Guided Product Exploration:** Create an interactive digital "concierge" experience that progressively introduces product lines based on first purchase signals
2. **Early-win Celebration:** Implement immediate recognition of their first successful product use with personalized congratulatory messages and next-step guidance
3. **Expectation-exceeding Delivery:** Include unexpected premium touches in first deliveries (handwritten note, sample, premium packaging) to create memorable unboxing
4. **Success Enablement Kit:** Bundle comprehensive getting-started resources with first purchase (how-to videos, insider tips, creative use ideas) to ensure product success
5. **Decision Validation Content:** Share personalized social proof and expert endorsements specifically related to their first purchase to reinforce their buying decision

## **Top Promising Customers**

In [44]:
-- Identifies Promising segment
-- Moderately recent customers with low frequency and spending
SELECT TOP 10 
    c.CustomerID, 
    p.FirstName + ' ' + p.LastName AS CustomerName, 
    st.Name AS Territory, 
    crfm.Recency AS DaysSinceLastPurchase, 
    crfm.Frequency AS PurchaseCount, 
    crfm.Monetary AS TotalSpend, 
    crfm.LastPurchaseDate,
    'Promising' AS CustomerSegment
FROM 
    Sales.Customer c 
    JOIN Person.Person p ON c.PersonID = p.BusinessEntityID 
    JOIN Sales.SalesTerritory st ON c.TerritoryID = st.TerritoryID 
    JOIN (
        SELECT 
            c.CustomerID, 
            DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) AS Recency, 
            COUNT(DISTINCT soh.SalesOrderID) AS Frequency, 
            SUM(soh.TotalDue) AS Monetary, 
            MAX(soh.OrderDate) AS LastPurchaseDate,
            NTILE(5) OVER (ORDER BY DATEDIFF(DAY, MAX(soh.OrderDate), CONVERT(DATE, GETDATE())) ASC) AS R_Score,
            NTILE(5) OVER (ORDER BY COUNT(DISTINCT soh.SalesOrderID) DESC) AS F_Score,
            NTILE(5) OVER (ORDER BY SUM(soh.TotalDue) DESC) AS M_Score
        FROM 
            Sales.Customer c 
            JOIN Sales.SalesOrderHeader soh ON c.CustomerID = soh.CustomerID 
        GROUP BY 
            c.CustomerID
    ) crfm ON c.CustomerID = crfm.CustomerID 
WHERE 
    crfm.R_Score >= 3  -- Moderate recency score
    AND crfm.R_Score < 4  -- But not highest recency
    AND crfm.F_Score <= 2  -- Low frequency score
    AND crfm.M_Score <= 2  -- Low monetary score
ORDER BY 
    crfm.Recency ASC;

(10 rows affected)

Total execution time: 00:00:00.225

CustomerID CustomerName Territory DaysSinceLastPurchase PurchaseCount TotalSpend LastPurchaseDate CustomerSegment 15778 José Miller Northwest 4101 2 3511.6459 2014-02-21 00:00:00.000 Promising 15964 Steven Cox Southwest 4101 2 3445.3459 2014-02-21 00:00:00.000 Promising 18163 Gabriel Zhang France 4101 2 3363.6844 2014-02-21 00:00:00.000 Promising 16532 Tommy Sharma France 4101 2 5438.4675 2014-02-21 00:00:00.000 Promising 19034 Tabitha Diaz Germany 4101 2 3671.6028 2014-02-21 00:00:00.000 Promising 14301 Ruben Vazquez Australia 4101 3 5682.7384 2014-02-21 00:00:00.000 Promising 12007 Shannon Sun Australia 4101 3 7761.277 2014-02-21 00:00:00.000 Promising 26154 Cory Madan Australia 4101 2 2142.0094 2014-02-21 00:00:00.000 Promising 12677 Cedric Liu Australia 4101 3 7497.944 2014-02-21 00:00:00.000 Promising 12609 Linda Carlson United Kingdom 4101 3 6228.7726 2014-02-21 00:00:00.000 Promising

**Recommendations for Promising Customers:**

1. **Value Discovery Pathway:** Create a personalized "value escalator" showing progressive benefits they'll unlock with each additional interaction with your brand
2. **Preference Mapping Technology:** Implement AI-driven tools that analyze initial purchase signals to create hyper-relevant next product recommendations
3. **Micro-commitment Challenges:** Design a series of small engagement steps (product reviews, social shares, feature exploration) each rewarded with increasing benefits
4. **Early Brand Story Immersion:** Develop interactive content experiences that emotionally connect customers to your brand values and origin story
5. **Targeted Category Education:** Provide specialized learning resources about complementary product categories most relevant to their initial interests